# Интуиция принципа работы градиентного бустинга

Рассмотрим "игрушечный" пример того, как работает и обучается градиентный бустинг. 

В данной демонстрации мы допускаем упрощения в угоду понятности и интуитивности, первоочередная цель это дать ответы на вопросы:
* Как пошагово обучается градиентный бустинг?
* Что получают на вход модели в градиентном бустинге?
* Что предсказывают модели в градиентном бустинге?
* Где градиент в градиентном бустинге?


Будем решать задачу регрессии, для начала сгенерируем датасет, создадим 10 объектов с 3 признаками и целевой переменной:

In [ ]:
from sklearn.datasets import make_regression
import numpy as np

np.random.seed(0)
x, y = make_regression(n_samples=10, n_features=3)

In [ ]:
print(f'x.shape: {x.shape}\nx:\n {x}')

In [ ]:
print(f'y.shape: {y.shape}\ny:\n {y}')

Отобразим данные в DaraFrame для наглядности:

In [ ]:
import pandas as pd

df = pd.DataFrame(x, columns=['feature_1', 'feature_2', 'feature_3'])
df['y_true'] = y

In [ ]:
df

**Шаг 0.**

Делаем самое первое предсказание, от которого сможем шагать дальше. Самое наивное, что можно сделать это предсказать среднее:

In [ ]:
df['y_pred_0'] = df['y_true'].mean()

In [ ]:
df

Теперь посчитаем нашу ошибку по всем объектам, будем использовать mean squared error

 $MSE:$  $\large \frac1n \sum_{i=1}^{n}(x_i-y_i)^2$

In [ ]:
from sklearn.metrics import mean_squared_error

print(mean_squared_error(df['y_pred_0'], df['y_true']))

**Шаг 1.**

Посчитаем градиент со знаком минус (антиградиент):

In [ ]:
df['-grad_0'] = -2*(df['y_pred_0'] - df['y_true'])

In [ ]:
df

**Шаг 2.**

Создадим простой предикатор (возьмем дерево глубиной равной единице). Обучим дерево восстанавливать антиградиент. В качестве входных данных - наши признаки, в качестве целевой переменной - антиградиент.

In [ ]:
from sklearn.tree import DecisionTreeRegressor

tree_1 = DecisionTreeRegressor(max_depth=1)

tree_1.fit(df[['feature_1', 'feature_2', 'feature_3']], df['-grad_0'])

Делаем предсказание нашего дерева:

In [ ]:
df['tree_pred_1'] = tree_1.predict(df[['feature_1', 'feature_2', 'feature_3']])

In [ ]:
df

Посмотрим подробнее по какому правилу дерево делает предсказание:

In [ ]:
from sklearn.tree import plot_tree
import matplotlib.pyplot as plt

plot_tree(tree_1)
plt.show()

**Шаг 3.**

Делаем шаг к искомой целевой переменной. Умножаем предсказание дерева на шаг (`learning rate = lr`) и прибавляем к нашему предыдущему прогнозу.

In [ ]:
lr = 0.1

df['y_pred_1'] = df['y_pred_0'] + lr*df['tree_pred_1']

In [ ]:
df

Видно, что для каких то объектов стало лучше, для каких то - хуже. Сравним общее качество после первой итерации:

In [ ]:
mse_0 = mean_squared_error(df['y_true'], df['y_pred_0'])
mse_1 = mean_squared_error(df['y_true'], df['y_pred_1'])

print(f'Iteration №0, mse: {mse_0}')
print(f'Iteration №1, mse: {mse_1}')


Отлично, стало лучше! Повторим шаги с 1 по 3

**Шаг 1.**

Считаем антиградиент от последнего предсказания `y_pred_1`

In [ ]:
df['-grad_1'] = -2*(df['y_pred_1'] - df['y_true'])

In [ ]:
df

**Шаг 2.**

Создаем второе дерево, учим на новом антиградиенте:

In [ ]:
tree_2 = DecisionTreeRegressor(max_depth=1)

tree_2.fit(df[['feature_1', 'feature_2', 'feature_3']], df['-grad_1'])

**Шаг 3.**

Шагаем в сторону антиградиента:

In [ ]:
df['y_pred_2'] = df['y_pred_1'] + lr * tree_2.predict(df[['feature_1', 'feature_2', 'feature_3']])

In [ ]:
df

Сравним качество на всех итерациях:

In [ ]:
mse_1 = mean_squared_error(df['y_true'], df['y_pred_1'])
mse_2 = mean_squared_error(df['y_true'], df['y_pred_2'])

print(f'Iteration №0, mse: {mse_0}')
print(f'Iteration №1, mse: {mse_1}')
print(f'Iteration №2, mse: {mse_2}')

Видим, что качество предсказания улучшается, напишем цикл, чтобы можно было выбрать большее количество итераций:

In [ ]:
df = df[['feature_1', 'feature_2', 'feature_3', 'y_true']].copy()

In [ ]:
df

In [ ]:
n_estimators = 100
lr = 0.1
#trees = []
plot_err = []

# step 0
df['y_pred'] = df['y_true'].mean() 

for i in range(n_estimators):
    # step 1
    df['-grad'] = -2*(df['y_pred'] - df['y_true'])
    # step 2
    tree = DecisionTreeRegressor(max_depth=1)
    tree.fit(df[['feature_1', 'feature_2', 'feature_3']], df['-grad'])
    # step 3
    df['y_pred'] =  df['y_pred'] + lr*tree.predict(df[['feature_1', 'feature_2', 'feature_3']]) 
    #trees.append(tree)
    if i % (n_estimators / 10) == 0:
        print(mean_squared_error(df['y_true'], df['y_pred'])) 
    plot_err.append(mean_squared_error(df['y_true'], df['y_pred']))


In [ ]:
plt.figure(figsize=(10, 5))
plt.plot(plot_err)
plt.ylabel('err')
plt.xlabel('n_estimators')
plt.show()